In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import librosa
import os
import shutil
# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/music-midi-dataset/x (43).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (26).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (30).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (50).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (12).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (5).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (47).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (32).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (9).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (7).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (18).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (31).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (39).mid
/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (21).mid
/kaggle/input/music-midi-dataset/midi_dataset/mid

In [2]:
pip install pretty_midi

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 51.8 MB/s eta 0:00:0000:0100:01
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.6/54.6 kB 4.1 MB/s eta 0:00:00
  Created wheel for pretty_midi: filename=pretty_midi-0.2.10-py3-none-any.whl size=5592286 sha256=30518d40c7bf7101680da72355dedce85bcfcf9311a029eb09e434d2e7716fd8
  Stored in directory: /root/.cache/pip/wheels/e6/95/ac/15ceaeb2823b04d8e638fd1495357adb8d26c00ccac9d7782e
Successfully built pretty_midi
Note: you may need to restart the kernel to use updated packages.


In [3]:
import pretty_midi

In [4]:
def midi_to_events(midi):
    events = []
    for instrument in midi.instruments:
        if not instrument.is_drum:
            for note in instrument.notes:
                events.append(('note_on', note.start, note.pitch))
                events.append(('note_off', note.end, note.pitch))
    return sorted(events, key=lambda x: x[1])  # sort by time

In [5]:
def add_time_shifts(events, quantization=0.01):
    token_seq = []
    prev_time = 0.0

    for event_type, time, pitch in events:
        delta_time = time - prev_time
        shift_steps = int(delta_time / quantization)

        if shift_steps > 0:
            token_seq.append(f"time_shift_{shift_steps}")
        
        if event_type == "note_on":
            token_seq.append(f"note_on_{pitch}")
        elif event_type == "note_off":
            token_seq.append(f"note_off_{pitch}")

        prev_time = time

    return token_seq

In [7]:
path = "/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset/x (1).mid"
midi = pretty_midi.PrettyMIDI(path)
events = midi_to_events(midi)
token_seq = add_time_shifts(events)

In [8]:
src_dir = "/kaggle/input/music-midi-dataset/midi_dataset/midi_dataset"

# Token collection
all_tokens = []
midi_files = [f for f in os.listdir(src_dir) if f.lower().endswith('.mid')]

for i, midi_file in enumerate(midi_files):
    full_path = os.path.join(src_dir, midi_file)
    midi = pretty_midi.PrettyMIDI(full_path)
    events = midi_to_events(midi)
    tokens = add_time_shifts(events)
    all_tokens.extend(tokens)
    #print(f"Processed {i+1}/{len(midi_files)}: {midi_file}")

vocab = sorted(set(all_tokens))
token_to_id = {tok: i for i, tok in enumerate(vocab)}
id_to_token = {i: tok for tok, i in token_to_id.items()}
print(id_to_token)

{0: 'note_off_25', 1: 'note_off_26', 2: 'note_off_28', 3: 'note_off_29', 4: 'note_off_30', 5: 'note_off_31', 6: 'note_off_32', 7: 'note_off_33', 8: 'note_off_34', 9: 'note_off_35', 10: 'note_off_36', 11: 'note_off_37', 12: 'note_off_38', 13: 'note_off_39', 14: 'note_off_40', 15: 'note_off_41', 16: 'note_off_42', 17: 'note_off_43', 18: 'note_off_44', 19: 'note_off_45', 20: 'note_off_46', 21: 'note_off_47', 22: 'note_off_48', 23: 'note_off_49', 24: 'note_off_50', 25: 'note_off_51', 26: 'note_off_52', 27: 'note_off_53', 28: 'note_off_54', 29: 'note_off_55', 30: 'note_off_56', 31: 'note_off_57', 32: 'note_off_58', 33: 'note_off_59', 34: 'note_off_60', 35: 'note_off_61', 36: 'note_off_62', 37: 'note_off_63', 38: 'note_off_64', 39: 'note_off_65', 40: 'note_off_66', 41: 'note_off_67', 42: 'note_off_68', 43: 'note_off_69', 44: 'note_off_70', 45: 'note_off_71', 46: 'note_off_72', 47: 'note_off_73', 48: 'note_off_74', 49: 'note_off_75', 50: 'note_off_76', 51: 'note_off_77', 52: 'note_off_78', 53

In [9]:
import keras
from keras.preprocessing.sequence import pad_sequences

token_ids = [token_to_id[tok] for tok in token_seq]
input_seq = pad_sequences([token_ids], maxlen=256, padding='post')
print(token_ids)

2025-06-29 11:08:22.879936: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751195303.048196      35 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751195303.095723      35 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


[112, 109, 104, 165, 41, 38, 33, 116, 100, 112, 165, 45, 29, 41, 112, 109, 105, 165, 41, 38, 34, 100, 95, 104, 144, 104, 144, 29, 24, 33, 33, 112, 109, 104, 116, 178, 119, 163, 45, 156, 48, 156, 121, 179, 50, 116, 205, 45, 112, 170, 41, 38, 33, 112, 100, 116, 41, 116, 179, 45, 119, 179, 48, 121, 179, 50, 116, 205, 45, 170, 41, 29, 45, 105, 109, 112, 116, 179, 45, 119, 179, 48, 121, 179, 50, 116, 194, 45, 114, 179, 43, 112, 156, 34, 38, 41, 104, 95, 100, 41, 116, 179, 45, 119, 179, 48, 121, 179, 104, 50, 116, 205, 45, 170, 33, 33, 24, 29, 112, 109, 104, 116, 179, 45, 119, 179, 48, 121, 179, 50, 124, 179, 53, 123, 179, 52, 121, 156, 50, 119, 156, 41, 38, 33, 116, 100, 112, 179, 48, 116, 179, 45, 117, 179, 46, 119, 205, 48, 170, 45, 29, 41, 105, 109, 112, 116, 179, 45, 119, 179, 48, 121, 179, 50, 116, 194, 45, 114, 179, 43, 112, 156, 34, 38, 41, 104, 95, 100, 41, 116, 179, 45, 114, 179, 43, 112, 179, 104, 41, 112, 179, 41, 201, 33, 33, 24, 29, 112, 109, 104, 116, 179, 45, 119, 179, 48, 12

In [10]:
sequence_length = 100
X = []
y = []

for i in range(len(token_ids) - sequence_length):
    seq_in = token_ids[i : i + sequence_length]
    seq_out = token_ids[i + sequence_length]
    X.append(seq_in)
    y.append(seq_out)

In [11]:
X = np.array(X)
y = np.array(y)

In [12]:
from keras.models import Sequential
from keras.layers import Embedding, LSTM, Dense

vocab_size = len(token_to_id)
sequence_length = 100  # use your actual sequence length

model = Sequential([
    Embedding(input_dim=vocab_size, output_dim=256, input_length=sequence_length),
    
    # First LSTM layer returns the full sequence
    LSTM(512, return_sequences=True),

    # Second LSTM layer returns only the final output
    LSTM(512),

    # Final dense layer maps to vocabulary size
    Dense(vocab_size, activation='softmax')
])

model.compile(loss='sparse_categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# Build the model explicitly (optional if using model.fit)
model.build(input_shape=(None, sequence_length))

model.summary()


/usr/local/lib/python3.11/dist-packages/keras/src/layers/core/embedding.py:90: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(
I0000 00:00:1751195328.586725      35 gpu_device.cc:2022] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 13942 MB memory:  -> device: 0, name: Tesla T4, pci bus id: 0000:00:04.0, compute capability: 7.5
I0000 00:00:1751195328.587402      35 gpu_device.cc:2022] Created device /job:localhost/replica:0/task:0/device:GPU:1 with 13942 MB memory:  -> device: 1, name: Tesla T4, pci bus id: 0000:00:05.0, compute capability: 7.5


Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━┓
┃ Layer (type)                         ┃ Output Shape                ┃         Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━┩
│ embedding (Embedding)                │ (None, 100, 256)            │          54,016 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ lstm (LSTM)                          │ (None, 100, 512)            │       1,574,912 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ lstm_1 (LSTM)                        │ (None, 512)                 │       2,099,200 │
├──────────────────────────────────────┼─────────────────────────────┼─────────────────┤
│ dense (Dense)                        │ (None, 211)                 │         108,243 │
└──────────────────────────────────────┴─────────────────────────────┴─────────────────┘

 Total params: 3,836,371 (14.63 MB)

 Trainable params: 3,836,371 (14.63 MB)

 Non-trainable params: 0 (0.00 B)

In [14]:
model.fit(X, y, epochs=50, batch_size=64)

Epoch 1/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 59ms/step - accuracy: 0.9888 - loss: 0.0299
Epoch 2/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 54ms/step - accuracy: 0.9937 - loss: 0.0279
Epoch 3/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 54ms/step - accuracy: 0.9933 - loss: 0.0263
Epoch 4/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 54ms/step - accuracy: 0.9812 - loss: 0.0452
Epoch 5/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 54ms/step - accuracy: 0.9839 - loss: 0.0719
Epoch 6/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 54ms/step - accuracy: 0.9869 - loss: 0.0618
Epoch 7/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 55ms/step - accuracy: 0.9861 - loss: 0.0673
Epoch 8/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 54ms/step - accuracy: 0.9878 - loss: 0.0487
Epoch 9/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 55ms/step - accuracy: 0.9899 - loss: 0.0447
Epoch 10/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 54ms/step - accuracy: 0.9932 - loss: 0.0363
Epoch 11/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 54ms/step - accuracy: 0.9917 - loss: 0.0299
Epoch 12/50
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 54ms/step - accuracy:

In [15]:
import random
seed_index = random.randint(0, len(X) - 1)
seed_seq = X[seed_index].tolist()  # shape: [sequence_length]

In [16]:
def generate_tokens(model, seed_seq, id_to_token, length=200):
    generated = seed_seq.copy()

    for _ in range(length):
        input_seq = np.array(generated[-sequence_length:]).reshape(1, sequence_length)
        preds = model.predict(input_seq, verbose=0)[0]

        # Sample the next token (argmax or probabilistic sampling)
        next_token_id = np.argmax(preds)
        generated.append(next_token_id)

    return [id_to_token[i] for i in generated]

In [17]:
generated_tokens = generate_tokens(model, seed_seq, id_to_token, length=300)
print("Generated token sequence:\n", generated_tokens[:50])

Generated token sequence:
 ['time_shift_33', 'note_off_76', 'note_on_71', 'time_shift_75', 'note_off_71', 'time_shift_25', 'note_off_67', 'note_off_55', 'note_off_71', 'note_on_60', 'note_on_64', 'note_on_67', 'note_on_71', 'time_shift_33', 'note_off_71', 'note_on_74', 'time_shift_33', 'note_off_74', 'note_on_76', 'time_shift_33', 'note_off_76', 'note_on_71', 'time_shift_50', 'note_off_71', 'note_on_69', 'time_shift_33', 'note_off_69', 'note_on_67', 'time_shift_16', 'note_off_60', 'note_off_64', 'note_off_67', 'note_on_59', 'note_on_50', 'note_on_55', 'note_off_67', 'note_on_71', 'time_shift_33', 'note_off_71', 'note_on_74', 'time_shift_33', 'note_off_74', 'note_on_76', 'time_shift_33', 'note_on_59', 'note_off_76', 'note_on_71', 'time_shift_75', 'note_off_71', 'time_shift_25']


In [18]:
def tokens_to_midi(tokens, output_path="generated_output.mid", duration_unit=0.01):
    midi = pretty_midi.PrettyMIDI()
    piano = pretty_midi.Instrument(program=0)
    current_time = 0.0
    active_notes = {}

    for token in tokens:
        if token.startswith("time_shift"):
            shift = int(token.split("_")[2])
            current_time += shift * duration_unit
        elif token.startswith("note_on"):
            pitch = int(token.split("_")[2])
            active_notes[pitch] = current_time
        elif token.startswith("note_off"):
            pitch = int(token.split("_")[2])
            if pitch in active_notes:
                start_time = active_notes[pitch]
                note = pretty_midi.Note(velocity=80, pitch=pitch, start=start_time, end=current_time)
                piano.notes.append(note)
                del active_notes[pitch]

    midi.instruments.append(piano)
    midi.write(output_path)


In [19]:
tokens_to_midi(generated_tokens, output_path="generated.mid")

In [24]:
!apt-get install -y fluidsynth
!pip install pyfluidsynth

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
fluidsynth is already the newest version (2.2.5-1).
0 upgraded, 0 newly installed, 0 to remove and 87 not upgraded.


In [32]:
def midi_to_wav(midi_path, wav_path, sf2_path):
    midi_data = pretty_midi.PrettyMIDI(midi_path)
    audio = midi_data.fluidsynth(sf2_path=sf2_path)
    
    # Save to WAV
    from scipy.io.wavfile import write
    sample_rate = 44100
    write(wav_path, sample_rate, audio)

In [33]:
import subprocess

def midi_to_wav_cli(midi_path, wav_path, sf2_path):
    cmd = [
        "fluidsynth",
        "-ni",
        sf2_path,
        midi_path,
        "-F",
        wav_path,
        "-r",
        "44100"
    ]
    subprocess.run(cmd, check=True)


In [34]:
midi_path = "/kaggle/working/generated.mid"
wav_path = "/kaggle/working/generated.wav"
sf2_path = "/kaggle/input/fluidr3-gm/FluidR3_GM.sf2"

midi_to_wav_cli(midi_path, wav_path, sf2_path)

FluidSynth runtime version 2.2.5
Copyright (C) 2000-2022 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of Creative Technology Ltd.

Rendering audio to file '/kaggle/working/generated.wav'..


In [35]:
from IPython.display import Audio
Audio(wav_path)

In [37]:
import random

def generate_tokens_with_mood(model, seed_seq, token_to_id, id_to_token, length=300, mood="MAJOR"):
    mood_token = f"[{mood.upper()}]"
    if mood_token in token_to_id:
        seed_seq = [token_to_id[mood_token]] + seed_seq
    generated = seed_seq.copy()

    for _ in range(length):
        input_seq = np.array(generated[-sequence_length:]).reshape(1, sequence_length)
        preds = model.predict(input_seq, verbose=0)[0]
        next_token_id = np.argmax(preds)
        generated.append(next_token_id)

    return [id_to_token[i] for i in generated]


In [38]:
N = 100  # generate 10 clips
for i in range(N):
    mood = "MAJOR" if i < N // 2 else "MINOR"
    seed_index = random.randint(0, len(X) - 1)
    seed = X[seed_index].tolist()

    tokens = generate_tokens_with_mood(model, seed, token_to_id, id_to_token, mood=mood)
    midi_name = f"gen_{i}_{mood.lower()}.mid"
    wav_name = f"gen_{i}_{mood.lower()}.wav"

    tokens_to_midi(tokens, midi_name)
    midi_to_wav_cli(midi_name, wav_name, sf2_path)

FluidSynth runtime version 2.2.5
Copyright (C) 2000-2022 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of Creative Technology Ltd.

Rendering audio to file 'gen_0_major.wav'..
FluidSynth runtime version 2.2.5
Copyright (C) 2000-2022 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of Creative Technology Ltd.

Rendering audio to file 'gen_1_major.wav'..
FluidSynth runtime version 2.2.5
Copyright (C) 2000-2022 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of Creative Technology Ltd.

Rendering audio to file 'gen_2_major.wav'..
FluidSynth runtime version 2.2.5
Copyright (C) 2000-2022 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of Creative Technology Ltd.

Rendering audio to file 'gen_3_major.wav'..
FluidSynth runtime version 2.2.5
Copyright (C) 2000-2022 Peter Hanappe and o

In [39]:
import librosa
import matplotlib.pyplot as plt
import numpy as np
import os

def save_spectrogram(wav_path, out_path):
    y, sr = librosa.load(wav_path, sr=44100)
    S = librosa.feature.melspectrogram(y=y, sr=sr)
    S_db = librosa.power_to_db(S, ref=np.max)

    plt.figure(figsize=(3, 3))
    plt.axis('off')
    librosa.display.specshow(S_db, sr=sr, cmap='magma')
    plt.savefig(out_path, bbox_inches='tight', pad_inches=0)
    plt.close()


In [40]:
for i in range(N):
    wav_file = f"gen_{i}_{'major' if i < N//2 else 'minor'}.wav"
    spec_file = f"spec_{i}_{'major' if i < N//2 else 'minor'}.png"
    save_spectrogram(wav_file, spec_file)


In [41]:
from PIL import Image
from sklearn.model_selection import train_test_split
import numpy as np

def load_images(folder):
    X, y = [], []
    for filename in os.listdir(folder):
        if filename.endswith(".png"):
            label = 0 if "minor" in filename else 1
            path = os.path.join(folder, filename)
            img = Image.open(path).resize((128, 128)).convert("RGB")
            X.append(np.array(img) / 255.0)
            y.append(label)
    return np.array(X), np.array(y)

X, y = load_images(".")
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)


In [50]:
from keras.models import Sequential
from keras.layers import Conv2D, Flatten, Dense
from keras.layers import AveragePooling2D

model = Sequential([
    Conv2D(32, (3, 3), activation='relu', input_shape=(128, 128, 3)),
    AveragePooling2D(2,2),
    Conv2D(64, (3, 3), activation='relu'),
    AveragePooling2D(2,2),
    Flatten(),
    Dense(64, activation='relu'),
    Dense(1, activation='sigmoid')  # binary
])

model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
model.fit(X_train, y_train, epochs=100, validation_data=(X_test, y_test))

Epoch 1/100
3/3 ━━━━━━━━━━━━━━━━━━━━ 4s 720ms/step - accuracy: 0.4422 - loss: 1.1178 - val_accuracy: 0.5000 - val_loss: 0.7807
Epoch 2/100
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step - accuracy: 0.4883 - loss: 0.7664 - val_accuracy: 0.5000 - val_loss: 0.6957
Epoch 3/100
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step - accuracy: 0.5508 - loss: 0.6831 - val_accuracy: 0.5000 - val_loss: 0.6953
Epoch 4/100
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step - accuracy: 0.5156 - loss: 0.6921 - val_accuracy: 0.5000 - val_loss: 0.6924
Epoch 5/100
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step - accuracy: 0.5633 - loss: 0.6893 - val_accuracy: 0.5000 - val_loss: 0.6908
Epoch 6/100
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step - accuracy: 0.5914 - loss: 0.6876 - val_accuracy: 0.5000 - val_loss: 0.6871
Epoch 7/100
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step - accuracy: 0.5617 - loss: 0.6850 - val_accuracy: 0.5000 - val_loss: 0.6812
Epoch 8/100
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step - accuracy: 0.6531 - loss: 0.6743 - val_accuracy: 0.5000 - val_loss

In [51]:
for i, layer in enumerate(model.layers):
    print(f"Layer {i}: {layer.name}")
    weights = layer.get_weights()
    for w in weights:
        print(w.shape)

Layer 0: conv2d_11
(3, 3, 3, 32)
(32,)
Layer 1: average_pooling2d_2
Layer 2: conv2d_12
(3, 3, 32, 64)
(64,)
Layer 3: average_pooling2d_3
Layer 4: flatten_4
Layer 5: dense_9
(57600, 64)
(64,)
Layer 6: dense_10
(64, 1)
(1,)


In [53]:
import numpy as np

weights_dict = {}
for i, layer in enumerate(model.layers):
    for j, w in enumerate(layer.get_weights()):
        weights_dict[f"{layer.name}_{j}"] = w

np.savez("lstm_weights_export.npz", **weights_dict)